In [ ]:
import sys
import os
from datetime import timedelta, datetime
import plotly.io as pio
from mockseries.seasonality.sinusoidal_seasonality import SinusoidalSeasonality

pio.templates.default = "ggplot2"

SCRIPT_DIR = os.path.abspath(os.path.join('..'))
sys.path.append(os.path.dirname(SCRIPT_DIR))
from features.steps.time_series_generator import generate_timeseries, NoiseConfig, SeasonalityConfig, TimeConfig, \
    MissingDataConfig
from mockseries.transition import LinearTransition, LambdaTransition
import plotly.graph_objects as go

['/Users/avattoly/.pyenv/versions/3.11.9/lib/python311.zip', '/Users/avattoly/.pyenv/versions/3.11.9/lib/python3.11', '/Users/avattoly/.pyenv/versions/3.11.9/lib/python3.11/lib-dynload', '', '/Users/avattoly/.pyenv/versions/3.11.9/lib/python3.11/site-packages', '/Users/avattoly/AIOPS/CDO/metric-generator-3/aiops_e2e', '/Users/avattoly/AIOPS/CDO/metric-generator-3/aiops_e2e']


In [3]:
def plot_timeseries(metrics, mode='lines'):
    fig = go.Figure()

    # Convert epoch time to datetime
    metrics['ds'] = metrics['ds'].apply(lambda x: datetime.fromtimestamp(x))

    # Add the trace to the figure
    fig.add_trace(
        go.Scatter(x=metrics['ds'], y=metrics['y'], mode=mode)
    )

    fig.show()

Default Behaviour

By default the switch tranisition will be immedeate 

In [4]:
metrics = generate_timeseries(
    TimeConfig(start_value=1, end_value=100, duration=timedelta(days=4), transition_start=timedelta(days=2)))

fig = go.Figure()

# Add the trace to the figure
fig.add_trace(
    go.Scatter(x=metrics['ds'], y=metrics['y'], mode='lines')
)

plot_timeseries(metrics)

Linear Transition 

transition start at dat and completes in 1 day duration . Complete duration is 4 days

In [5]:
metrics = generate_timeseries(TimeConfig(start_value=1, end_value=100,
                                         transition_start=timedelta(days=2),
                                         duration=timedelta(days=4),
                                         transition=LinearTransition(transition_window=timedelta(days=1))))
plot_timeseries(metrics)

Custom Transition

Custom transition can be added by using lambda tranistion . In below case we are applying a square function for transition 

In [6]:
metrics = generate_timeseries(TimeConfig(start_value=1,
                                         end_value=100,
                                         transition_start=timedelta(days=1),
                                         duration=timedelta(days=5),
                                         transition=LambdaTransition(
                                             transition_window=timedelta(days=2),
                                             transition_function=lambda x: x * x,
                                         )))

plot_timeseries(metrics)

Removing Noise

In [7]:
metrics = generate_timeseries(TimeConfig(start_value=1,
                                         end_value=100,
                                         transition_start=timedelta(days=1),
                                         duration=timedelta(days=5),
                                         transition=LambdaTransition(
                                             transition_window=timedelta(days=2),
                                             transition_function=lambda x: x * x,
                                         ),
                                         noise_config=NoiseConfig(enable=False)))

plot_timeseries(metrics)

Removing Seasonality

In [8]:
metrics = generate_timeseries(TimeConfig(start_value=1,
                                         end_value=100,
                                         transition_start=timedelta(days=1),
                                         duration=timedelta(days=5),
                                         transition=LambdaTransition(
                                             transition_window=timedelta(days=2),
                                             transition_function=lambda x: x * x,
                                         ),
                                         noise_config=NoiseConfig(enable=False)),
                              seasonality_config=SeasonalityConfig(enable=False))

plot_timeseries(metrics)

Adding missing data

In [9]:
metrics = generate_timeseries(
    TimeConfig(
        start_value=1,
        end_value=100,
        transition_start=timedelta(days=1),
        duration=timedelta(days=5),
        transition=LambdaTransition(
            transition_window=timedelta(days=2),
            transition_function=lambda x: x * x,
        ),
        noise_config=NoiseConfig(enable=False)),
    seasonality_config=SeasonalityConfig(enable=False),
    missing_data_configs=[
        MissingDataConfig(
            start_time=datetime.now() - timedelta(days=1),
            duration=timedelta(days=1),
            miss_probability=0.9
        )
    ]
)

plot_timeseries(metrics, mode="markers")

In [22]:
metrics = generate_timeseries(
    TimeConfig(
        start_value=111000,
        end_value=213000,
        transition_start=timedelta(days=0),
        duration=timedelta(days=31),
        transition=LambdaTransition(
            transition_window=timedelta(days=31),
            transition_function=lambda x: x * x,
        ),
        # noise_config=NoiseConfig(enable=False)
        ),
    seasonality_config=SeasonalityConfig(
    enable=True,
    seasonality_list=[SinusoidalSeasonality(amplitude=8000, period=timedelta(hours=12))],
),
)

plot_timeseries(metrics, mode="markers")